In [1]:
# Imports

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import glob

import scipy.signal
import holidays

import tensorflow as tf

from pandas.tseries.offsets import MonthEnd

import seaborn as sb

import IPython

In [2]:
# Aux Functions for Solcast and PV data processing

def get_solcast(path):
    file = pd.read_csv(path)
    file.index = pd.to_datetime(file['PeriodEnd'])
    file = file.resample('15T').pad()
    
    return file


def get_pv(path):
    file = pd.read_csv(path)
    file.index = pd.to_datetime(file['datetime_utc'])
    file = file.resample('15T').mean()
    
    return file


def get_solcastPV(df1, df2):
    '''
    df1: PV dataframe
    df2: Solcast dataframe
    '''
    
    # Filter both dataframes for 2019 and 2020
    try:
        temp_df1 = df1['2019':'2021-04-01']
        temp_df2 = df2['2019':'2021-04-01']
        
        # Check if data is complete. If not, match the smaller indexes
        if temp_df2.shape[0] < temp_df1.shape[0]:
            last_entry = temp_df2.index
            temp_df1 = temp_df1['2019':'{}'.format(temp_df2.index[-1].tz_convert(None))]


        # Only considering 2019 and 2020 since data is complete for that period
        temp_data = pd.DataFrame({'PV': temp_df1['pv'].values}, index=temp_df1.index)
        for i in np.arange(3, len(temp_df2.columns)):
            temp_data[temp_df2.columns[i]] = temp_df2[temp_df2.columns[i]].shift(-1).values
            
        return temp_data
    except:
        temp_df1 = df1['2019':'2020']
        temp_df2 = df2['2019':'2020']
        
        # Check if data is complete. If not, match the smaller indexes
        if temp_df2.shape[0] < temp_df1.shape[0]:
            last_entry = temp_df2.index
            temp_df1 = temp_df1['2019':'{}'.format(temp_df2.index[-1].tz_convert(None))]


        # Only considering 2019 and 2020 since data is complete for that period
        temp_data = pd.DataFrame({'PV': temp_df1['pv'].values}, index=temp_df1.index)
        for i in np.arange(3, len(temp_df2.columns)):
            temp_data[temp_df2.columns[i]] = temp_df2[temp_df2.columns[i]].shift(-1).values
            
        return temp_data

In [15]:
# Get data and build a dictionary for preprocessing

data = {}

folders = glob.glob('C:/Users/FEEL/Jupyter/ecgomes/upacs_study/data/*')
for folder in folders:
    # Load each of the files inside the folder
    temp_pv = get_pv('{}/pv.csv'.format(folder))
    temp_solcast = get_solcast('{}/solcast.csv'.format(folder))
    
    # Join the files into a single dataframe
    temp_upac = get_solcastPV(temp_pv, temp_solcast)
    
    temp_name = folder.split('\\')[1]
    data[temp_name] = temp_upac
    
    print('{} date range: {} - {}'.format(temp_name, temp_upac.index[0], temp_upac.index[-1]))

upac02 date range: 2019-01-01 00:00:00 - 2020-06-15 22:30:00
upac06 date range: 2019-01-01 00:00:00 - 2020-06-15 22:30:00
upac08 date range: 2019-01-01 00:00:00 - 2021-04-01 23:45:00
upac09 date range: 2019-01-01 00:00:00 - 2020-12-31 23:45:00
upac13 date range: 2019-01-01 00:00:00 - 2020-12-31 23:45:00


In [16]:
# Aux Functions for adding 2D time information

import datetime

def days_2d(df):
    '''
    Adds 2D time information for single days
    df: dataframe to add the information
    '''
    # Map the index into seconds
    timestamp_s = pd.to_datetime(df.index.values).map(datetime.datetime.timestamp)
    
    # Since we're calculating the cos and sin values from seconds, it's 60 seconds into 60 min into 24 hours per day
    day_calc = 24*60*60
    
    # Calculate the values
    dayx = np.cos((2*np.pi/day_calc) * timestamp_s)
    dayy = np.sin((2*np.pi/day_calc) * timestamp_s)
    
    return dayx, dayy
    

def years_2d(df):
    '''
    Adds 2D time representation throught a year
    df: dataframe to add the information
    '''
    # Add Year Information

    day_year = df.index.dayofyear
    year_constant = 365.2524

    yearx = np.cos((2*np.pi/year_constant) * day_year)
    yeary = np.sin((2*np.pi/year_constant) * day_year)
    
    return yearx, yeary

In [17]:
# Add the 2D time information to the data

for upac in data.keys():
    dayx, dayy = days_2d(data[upac])
    yearx, yeary = years_2d(data[upac])
    
    data[upac]['Day X'] = dayx
    data[upac]['Day Y'] = dayy
    
    data[upac]['Year X'] = yearx
    data[upac]['Year Y'] = yeary

In [18]:
# Split the data for training, validation and testing

data_train = {}
data_val = {}
data_test = {}

for upac in data.keys():
    data_train[upac] = data[upac]['2019']
    data_val[upac] = data[upac]['2020-01':'2020-03']
    data_test[upac] = data[upac]['2020-04':]

C:\Users\FEEL\AppData\Local\Temp/ipykernel_9884/2785044146.py:8: FutureWarning: Indexing a DataFrame with a datetimelike index using a single string to slice the rows, like `frame[string]`, is deprecated and will be removed in a future version. Use `frame.loc[string]` instead.
  data_train[upac] = data[upac]['2019']


In [19]:
# Aux Function for filtering data

def filter_by_points(df, frequency='D', num_points=1440, return_dictionary=False):
    
    df_dropped = df.dropna()
    grouper = df_dropped.groupby(pd.Grouper(freq=frequency))
    
    output = 0
    if return_dictionary:
        new_dict = {}
        for i in grouper:
            if (len(i[1]) != num_points):
                pass
            else:
                new_dict[i[0]] = pd.DataFrame(i[1])
        output = new_dict
    else:
        new_df = pd.DataFrame({})
        for i in grouper:
            if (len(i[1]) != num_points):
                pass
            else:
                new_df = new_df.append(pd.DataFrame(i[1]))
        output = new_df
            
    return output

In [20]:
# Filter the data by number of points that should be present in a single day

filtered_train = {}
filtered_val = {}
filtered_test = {}

for upac in data_train.keys():
    filtered_train[upac] = filter_by_points(data_train[upac], frequency='D', num_points=1440/15)
    filtered_val[upac] = filter_by_points(data_val[upac], frequency='D', num_points=1440/15)
    filtered_test[upac] = filter_by_points(data_test[upac], frequency='D', num_points=1440/15)

In [21]:
# Select columns to use

USED_COLUMNS = ['PV', 
                'AirTemp', 
                'CloudOpacity',
                'Ghi',
                'GtiFixedTilt', 
                'Day Y', 'Day X',
                'Year Y', 'Year X']

In [22]:
# Data Normalization
# We don't want to normalize PV so we can capture diferences more easily

# Feature range
# PV - greater than 0
# AirTemp - Unchanged
# Cloud Opacity and Ghi - between 0 and 1
# Day X, Y and Year X and Y - already between -1 and 1

MAX_OPACITY = 100
MAX_GHI = 1023
MAX_GTI = 1071

normalized_train = {}
normalized_val = {}
normalized_test = {}

for upac in filtered_train.keys():
    normalized_train[upac] = filtered_train[upac][USED_COLUMNS].copy(deep=True)
    normalized_val[upac] = filtered_val[upac][USED_COLUMNS].copy(deep=True)
    normalized_test[upac] = filtered_test[upac][USED_COLUMNS].copy(deep=True)
    
    normalized_train[upac]['CloudOpacity'] = normalized_train[upac]['CloudOpacity'] / MAX_OPACITY
    normalized_val[upac]['CloudOpacity'] = normalized_val[upac]['CloudOpacity'] / MAX_OPACITY
    normalized_test[upac]['CloudOpacity'] = normalized_test[upac]['CloudOpacity'] / MAX_OPACITY
    
    normalized_train[upac]['Ghi'] = normalized_train[upac]['Ghi'] / MAX_GHI
    normalized_val[upac]['Ghi'] = normalized_val[upac]['Ghi'] / MAX_GHI
    normalized_test[upac]['Ghi'] = normalized_test[upac]['Ghi'] / MAX_GHI
    
    normalized_train[upac]['GtiFixedTilt'] = normalized_train[upac]['GtiFixedTilt'] / MAX_GTI
    normalized_val[upac]['GtiFixedTilt'] = normalized_val[upac]['GtiFixedTilt'] / MAX_GTI
    normalized_test[upac]['GtiFixedTilt'] = normalized_test[upac]['GtiFixedTilt'] / MAX_GTI

In [25]:
# Aux Function DNN Specific - Data Reshaping and Windowing

def split_sequence(sequence, n_steps, n_intervals):
    X = list()
    for i in np.arange(0, len(sequence), n_intervals):
        # find the end of this pattern
        end_ix = i + n_steps
        # check if we are beyond the sequence
        if end_ix > len(sequence) - 1:
            break
        # gather input and output parts of the pattern
        seq_x = sequence[i:end_ix]
        X.append(seq_x)
    return np.array(X)

def split_dataframe(df, input_width):
    current_list = []
    for i in df.columns[1:]:
        current_sequence = split_sequence(df[i], input_width, 1)
        current_list.append(current_sequence)
        
    stacked_list = np.stack(current_list, axis=-1)
    
    return stacked_list


def do_windowing(df, input_width=1, y_col='PV'):
    '''
    Perform the windowing on the dataframe
    df: input dataframe to perform windowing
    input_width: temporal dimension size or number of timesteps
    y_col: name of column for the prediction
    '''
    
    temp_x = split_dataframe(df, input_width)
    temp_y = df[y_col].values[input_width-1:-1]
    
    return temp_x, temp_y

In [26]:
# Do windowing on the data

X_train = {}
y_train = {}

X_val = {}
y_val = {}

X_test = {}
y_test = {}

for upac in normalized_train.keys():
    trainx = normalized_train[upac].drop('PV', axis=1)
    trainy = normalized_train[upac]['PV']
    valx = normalized_val[upac].drop('PV', axis=1)
    valy = normalized_val[upac]['PV']
    testx = normalized_test[upac].drop('PV', axis=1)
    testy = normalized_test[upac]['PV']
    
    X_train[upac] = trainx
    X_val[upac] = valx
    X_test[upac] = testx
    
    y_train[upac] = trainy
    y_val[upac] = valy
    y_test[upac] = testy

In [27]:
# Aux Functions to compile the model and add necessary info

def compile_and_fit(model, train_x, train_y, val_x, val_y,
                    max_epochs=1000, es_patience=200, rlr_patience=100, 
                    adam_lr=0.001):
    early_stopping = tf.keras.callbacks.EarlyStopping(monitor='val_loss',
                                                      patience=es_patience,
                                                      mode='min')
    
    reduce_lr = tf.keras.callbacks.ReduceLROnPlateau(monitor='val_loss',
                                                     patience=rlr_patience)

    model.compile(loss=tf.keras.losses.mean_squared_error,
                  optimizer=tf.optimizers.Adam(learning_rate=adam_lr),
                  metrics=[tf.metrics.MeanAbsoluteError(name='mae')])

    history = model.fit(train_x, train_y,
                        batch_size=32,
                        epochs=max_epochs,
                        validation_data=(val_x, val_y),
                        callbacks=[early_stopping, reduce_lr])
    return history

In [37]:
# Aux Function for predicting and storing values

def do_predictions(dictionary, save_path, X, y, index):
    # Go through each model in the dictionary
    for model in dictionary.keys():
        print('Doing {}'.format(model))
        
        temp_path = '{}/{}.csv'.format(save_path, model)
        
        y_pred = dictionary[model].predict(X, verbose=1)
        y_pred = pd.DataFrame(y_pred[:, :], columns=['PV'],
                              index=index)
        
        y_pred.to_csv(temp_path)
        
    # Also save ground-truth data at the end of the loop
    y_true = pd.DataFrame(y, columns=['PV'],
                          index=index)
    
    temp_path_gt = '{}/gt.csv'.format(save_path)
    y_true.to_csv(temp_path_gt)
    
    
def predict_upacs(model_dictionary, upac_name, X_train, y_train, X_val, y_val, X_test, y_test):
    # Simply call the function above for each of the settings to simplify
    
    print('Doing training for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi+gti/train'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_train[upac_name], 
                   y=y_train[upac_name],
                   index=normalized_train[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing validation for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi+gti/val'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_val[upac_name], 
                   y=y_val[upac_name],
                   index=normalized_val[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing testing for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi+gti/test'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_test[upac_name], 
                   y=y_test[upac_name],
                   index=normalized_test[upac_name].index)
    IPython.display.clear_output()

In [28]:
# Import the TabNet implementation

# From: https://github.com/titu1994/tf-TabNet
from tabnet import StackedTabNetRegressor

In [29]:
# Optuna for TabNet hyperparameter optimization

import optuna
import sklearn

import random

random.seed(69)
np.random.seed(69)
tf.random.set_seed(69)

def optuna_create_model(trial):
    # Do search for n_estimators, max_depth, reg_alpha and reg_lambda
    #sug_layers = trial.suggest_int('num_layers', 1, 4)
    sug_fdim = trial.suggest_int('feature_dim', 32, 72)
    sug_odim = trial.suggest_int('output_dim', 4, 12)
    sug_dsteps = trial.suggest_int('num_decision_steps', 1, 4)
    
    sug_model = StackedTabNetRegressor(feature_columns=None,
                                       num_layers=1, #sug_layers,
                                       num_regressors=1, 
                                       feature_dim=sug_fdim,
                                       num_features=8, 
                                       output_dim=sug_odim,
                                       num_decision_steps=sug_dsteps,
                                       num_groups=1)
    
    return sug_model


def optuna_create_training(model):
    compile_and_fit(model, X_train['upac08'], y_train['upac08'],
                    X_val['upac08'], y_val['upac08'],
                    max_epochs=50, rlr_patience=10, es_patience=20)
    
    
def optuna_create_evaluation(model):
    temp_yhat = model.predict(X_val['upac08'])
    return sklearn.metrics.mean_squared_error(y_val['upac08'], temp_yhat)
    
    
def objective(trial):
    # Instantiate the model
    temp_model = optuna_create_model(trial)
    
    # Train the model
    optuna_create_training(temp_model)
    
    # Evaluate model
    metrics_val = optuna_create_evaluation(temp_model)
    
    return metrics_val

study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=100, show_progress_bar=True)

[I 2022-07-28 17:25:53,444] A new study created in memory with name: no-name-27e8e2e1-11b9-4e22-a84f-9c9608c59f9b
c:\users\feel\jupyter\ecgomes\upacs_study\venv\lib\site-packages\optuna\progress_bar.py:47: ExperimentalWarning: Progress bar is experimental (supported from v1.2.0). The interface can change in the future.
  self._init_valid()


  0%|          | 0/100 [00:00<?, ?it/s]

Epoch 1/50
1089/1089 [==============================] - 3s 1ms/step - loss: 1644220.8750 - mae: 712.5095 - val_loss: 1243517.1250 - val_mae: 571.9921 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1270171.1250 - mae: 588.8021 - val_loss: 869593.1875 - val_mae: 448.4728 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 846714.3750 - mae: 457.0482 - val_loss: 545072.2500 - val_mae: 345.8116 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 1s 1ms/step - loss: 520005.1562 - mae: 349.7375 - val_loss: 334833.6562 - val_mae: 275.8424 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 1s 1ms/step - loss: 314046.1562 - mae: 275.6707 - val_loss: 220491.6094 - val_mae: 234.6279 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 1s 1ms/step - loss: 201929.0312 - mae: 226.8295 - val_loss: 171013.5469 - val_mae: 203.2840 - lr: 0.0010
Epoch 7/50
1089/1089 [=========

1089/1089 [==============================] - 6s 3ms/step - loss: 1539332.6250 - mae: 709.8397 - val_loss: 1071315.5000 - val_mae: 590.7015 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 3s 3ms/step - loss: 1017943.6875 - mae: 603.5064 - val_loss: 652014.4375 - val_mae: 487.1116 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 3s 3ms/step - loss: 633206.5625 - mae: 506.7497 - val_loss: 412604.8438 - val_mae: 408.3971 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 3s 3ms/step - loss: 423297.4062 - mae: 422.4138 - val_loss: 275590.8438 - val_mae: 332.1918 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 3s 3ms/step - loss: 318977.4375 - mae: 357.9543 - val_loss: 266444.7500 - val_mae: 301.8371 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 3s 3ms/step - loss: 264648.6562 - mae: 313.6446 - val_loss: 189899.2812 - val_mae: 256.7070 - lr: 0.0010
Epoch 7/50
1089/1089 [====================

1089/1089 [==============================] - 1s 961us/step - loss: 177707.5781 - mae: 211.6880 - val_loss: 164371.8906 - val_mae: 195.0402 - lr: 0.0010
Epoch 11/50
1089/1089 [==============================] - 1s 1ms/step - loss: 146464.0781 - mae: 193.3767 - val_loss: 141752.0625 - val_mae: 183.3438 - lr: 0.0010
Epoch 12/50
1089/1089 [==============================] - 1s 1ms/step - loss: 130319.1797 - mae: 183.2485 - val_loss: 141103.8594 - val_mae: 180.3042 - lr: 0.0010
Epoch 13/50
1089/1089 [==============================] - 1s 1ms/step - loss: 120939.0312 - mae: 176.2142 - val_loss: 131289.8281 - val_mae: 171.2925 - lr: 0.0010
Epoch 14/50
1089/1089 [==============================] - 1s 1ms/step - loss: 115419.4531 - mae: 170.4010 - val_loss: 140682.7344 - val_mae: 178.7161 - lr: 0.0010
Epoch 15/50
1089/1089 [==============================] - 1s 1ms/step - loss: 111087.3203 - mae: 165.2586 - val_loss: 118843.2734 - val_mae: 165.1264 - lr: 0.0010
Epoch 16/50
1089/1089 [===============

...

Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 877916.9375 - mae: 466.5342 - val_loss: 571933.7500 - val_mae: 354.0844 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 1s 1ms/step - loss: 549826.1875 - mae: 359.4031 - val_loss: 354730.1250 - val_mae: 283.9223 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 1s 1ms/step - loss: 335153.9688 - mae: 282.2054 - val_loss: 231477.1094 - val_mae: 235.9303 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 1s 1ms/step - loss: 214503.5312 - mae: 231.1784 - val_loss: 177484.3281 - val_mae: 204.6012 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 1s 1ms/step - loss: 156773.9844 - mae: 200.9562 - val_loss: 148042.1562 - val_mae: 197.3566 - lr: 0.0010
Epoch 8/50
1089/1089 [==============================] - 1s 1ms/step - loss: 131589.8906 - mae: 183.3357 - val_loss: 135455.0312 - val_mae: 173.0883 - lr: 0.0010
Epoch 9/50
1089/1089 [============

1089/1089 [==============================] - 1s 1ms/step - loss: 1762659.8750 - mae: 737.2343 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 8/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1762659.5000 - mae: 737.2341 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 9/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1762660.8750 - mae: 737.2333 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 10/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1762660.5000 - mae: 737.2344 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 11/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1762661.7500 - mae: 737.2343 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 12/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1762659.6250 - mae: 737.2341 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 1.0000e-04
Epoch 13/50
1089/1089 [===

1089/1089 [==============================] - 1s 1ms/step - loss: 101334.1016 - mae: 150.8113 - val_loss: 117390.6953 - val_mae: 155.1466 - lr: 0.0010
Epoch 34/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101344.1328 - mae: 149.8521 - val_loss: 118235.3359 - val_mae: 155.3277 - lr: 0.0010
Epoch 35/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101080.2969 - mae: 149.3747 - val_loss: 115674.1641 - val_mae: 155.7811 - lr: 0.0010
Epoch 36/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100833.5000 - mae: 149.0844 - val_loss: 116613.8281 - val_mae: 155.2500 - lr: 0.0010
Epoch 37/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100740.5625 - mae: 149.2563 - val_loss: 119233.0312 - val_mae: 157.4014 - lr: 0.0010
Epoch 38/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100579.5938 - mae: 149.3537 - val_loss: 117783.4141 - val_mae: 156.4431 - lr: 0.0010
Epoch 39/50
1089/1089 [=================

1089/1089 [==============================] - 1s 953us/step - loss: 103109.2109 - mae: 152.6537 - val_loss: 122287.9844 - val_mae: 159.6537 - lr: 0.0010
Epoch 32/50
1089/1089 [==============================] - 1s 950us/step - loss: 102527.1484 - mae: 152.2000 - val_loss: 125057.0703 - val_mae: 160.7544 - lr: 0.0010
Epoch 33/50
1089/1089 [==============================] - 1s 963us/step - loss: 102542.8438 - mae: 152.3172 - val_loss: 119137.9219 - val_mae: 154.9979 - lr: 0.0010
Epoch 34/50
1089/1089 [==============================] - 1s 958us/step - loss: 102312.9531 - mae: 151.3183 - val_loss: 118229.7266 - val_mae: 155.4985 - lr: 0.0010
Epoch 35/50
1089/1089 [==============================] - 1s 958us/step - loss: 102293.0234 - mae: 151.3698 - val_loss: 115868.8203 - val_mae: 153.7023 - lr: 0.0010
Epoch 36/50
1089/1089 [==============================] - 1s 954us/step - loss: 102032.2031 - mae: 150.8410 - val_loss: 120080.5469 - val_mae: 158.1883 - lr: 0.0010
Epoch 37/50
1089/1089 [=====

1089/1089 [==============================] - 1s 1ms/step - loss: 100490.0781 - mae: 148.6800 - val_loss: 122021.7500 - val_mae: 159.9740 - lr: 0.0010
Epoch 31/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100740.9062 - mae: 148.8645 - val_loss: 119193.2891 - val_mae: 155.9403 - lr: 0.0010
Epoch 32/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100170.2734 - mae: 148.2194 - val_loss: 120727.0000 - val_mae: 157.0236 - lr: 0.0010
Epoch 33/50
1089/1089 [==============================] - 1s 1ms/step - loss: 99980.1719 - mae: 148.7347 - val_loss: 114039.5938 - val_mae: 149.9245 - lr: 0.0010
Epoch 34/50
1089/1089 [==============================] - 1s 1ms/step - loss: 99814.1641 - mae: 147.4725 - val_loss: 116559.5703 - val_mae: 151.7974 - lr: 0.0010
Epoch 35/50
1089/1089 [==============================] - 1s 1ms/step - loss: 99866.5703 - mae: 147.5862 - val_loss: 113200.3203 - val_mae: 151.1515 - lr: 0.0010
Epoch 36/50
1089/1089 [====================

In [30]:
# TabNet best params (all fetures)

study.best_params

{'feature_dim': 39, 'output_dim': 11, 'num_decision_steps': 1}

In [52]:
# Train 10 Models for UPAC08 - Ghi + Gti

N_MODELS = 10
upac08_GhiGti = {}

for i in np.arange(N_MODELS):
    IPython.display.clear_output()
    print('Current Model: {:02d}'.format(i+1))
    
    tabnet_regressor = StackedTabNetRegressor(feature_columns=None,
                                              num_layers=1, #study.best_params['num_layers'],
                                              num_regressors=1, 
                                              feature_dim=study.best_params['feature_dim'],
                                              num_features=8, 
                                              output_dim=study.best_params['output_dim'],
                                              num_decision_steps=study.best_params['num_decision_steps'],
                                              num_groups=1)
    current_net_history = compile_and_fit(tabnet_regressor, 
                                          X_train['upac08'], y_train['upac08'],
                                          X_val['upac08'], y_val['upac08'])
    
    tabnet_regressor.save('models/tabnet/upac08_ghi+gti/Model {:02d}'.format(i+1), save_format='tf')
    upac08_GhiGti['Model {:02d}'.format(i+1)] = tabnet_regressor

Current Model: 10
Epoch 1/1000
1089/1089 [==============================] - 2s 1ms/step - loss: 1683373.7500 - mae: 723.4831 - val_loss: 1325536.8750 - val_mae: 599.8991 - lr: 0.0010
Epoch 2/1000
1089/1089 [==============================] - 1s 990us/step - loss: 1427492.3750 - mae: 636.8260 - val_loss: 1055557.2500 - val_mae: 511.7349 - lr: 0.0010
Epoch 3/1000
1089/1089 [==============================] - 1s 983us/step - loss: 1098625.3750 - mae: 535.4833 - val_loss: 772435.9375 - val_mae: 420.1260 - lr: 0.0010
Epoch 4/1000
1089/1089 [==============================] - 1s 986us/step - loss: 789114.3750 - mae: 438.2766 - val_loss: 538035.1875 - val_mae: 349.7845 - lr: 0.0010
Epoch 5/1000
1089/1089 [==============================] - 1s 988us/step - loss: 540932.0625 - mae: 357.4900 - val_loss: 369496.9062 - val_mae: 287.5862 - lr: 0.0010
Epoch 6/1000
1089/1089 [==============================] - 1s 989us/step - loss: 363482.8125 - mae: 295.1496 - val_loss: 262914.6875 - val_mae: 247.2044 - 

Epoch 100/1000
1089/1089 [==============================] - 1s 996us/step - loss: 95947.9453 - mae: 144.9673 - val_loss: 114853.3750 - val_mae: 151.5345 - lr: 0.0010
Epoch 101/1000
1089/1089 [==============================] - 1s 990us/step - loss: 95957.2031 - mae: 144.3083 - val_loss: 117249.2891 - val_mae: 158.0579 - lr: 0.0010
Epoch 102/1000
1089/1089 [==============================] - 1s 992us/step - loss: 95884.8438 - mae: 144.6686 - val_loss: 114655.5234 - val_mae: 153.1754 - lr: 0.0010
Epoch 103/1000
1089/1089 [==============================] - 1s 996us/step - loss: 95599.9062 - mae: 143.8682 - val_loss: 114821.5391 - val_mae: 158.0999 - lr: 0.0010
Epoch 104/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 95965.5703 - mae: 144.2820 - val_loss: 113084.6562 - val_mae: 156.4963 - lr: 0.0010
Epoch 105/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 95776.3047 - mae: 144.0966 - val_loss: 112360.8906 - val_mae: 152.6165 - lr: 0.0010
Epoch 10

1089/1089 [==============================] - 1s 983us/step - loss: 86315.2500 - mae: 134.8825 - val_loss: 121186.9453 - val_mae: 158.7616 - lr: 1.0000e-04
Epoch 199/1000
1089/1089 [==============================] - 1s 986us/step - loss: 86288.6328 - mae: 135.1067 - val_loss: 121389.0469 - val_mae: 158.5945 - lr: 1.0000e-04
Epoch 200/1000
1089/1089 [==============================] - 1s 986us/step - loss: 86222.1172 - mae: 134.8293 - val_loss: 121373.1641 - val_mae: 158.2470 - lr: 1.0000e-04
Epoch 201/1000
1089/1089 [==============================] - 1s 978us/step - loss: 86218.0859 - mae: 134.8083 - val_loss: 122102.6016 - val_mae: 159.7816 - lr: 1.0000e-04
Epoch 202/1000
1089/1089 [==============================] - 1s 972us/step - loss: 86198.2422 - mae: 134.9713 - val_loss: 120085.5234 - val_mae: 157.4258 - lr: 1.0000e-04
Epoch 203/1000
1089/1089 [==============================] - 1s 978us/step - loss: 86155.6797 - mae: 134.6796 - val_loss: 121697.4766 - val_mae: 158.8012 - lr: 1.0000

In [53]:
# UPAC08 Predictions for all features

predict_upacs(model_dictionary=upac08_GhiGti, 
              upac_name='upac08',
              X_train=X_train, y_train=y_train,
              X_val=X_val, y_val=y_val,
              X_test=X_test, y_test=y_test)

######################################

In [44]:
# Optuna for TabNet hyperparameter optimization - No Ghi, only tilted

import optuna
import sklearn

import random

random.seed(69)
np.random.seed(69)
tf.random.set_seed(69)

def optuna_create_model_tilt(trial):
    # Do search for n_estimators, max_depth, reg_alpha and reg_lambda
    #sug_layers = trial.suggest_int('num_layers', 1, 4)
    sug_fdim = trial.suggest_int('feature_dim', 32, 72)
    sug_odim = trial.suggest_int('output_dim', 4, 12)
    sug_dsteps = trial.suggest_int('num_decision_steps', 1, 4)
    
    sug_model = StackedTabNetRegressor(feature_columns=None,
                                       num_layers=1, #sug_layers,
                                       num_regressors=1, 
                                       feature_dim=sug_fdim,
                                       num_features=7, 
                                       output_dim=sug_odim,
                                       num_decision_steps=sug_dsteps,
                                       num_groups=1)
    
    return sug_model


def optuna_create_training_tilt(model):
    compile_and_fit(model, X_train['upac08'][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X',
                                              'Year Y', 'Year X']], y_train['upac08'],
                    X_val['upac08'][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X',
                                     'Year Y', 'Year X']], y_val['upac08'],
                    max_epochs=50, rlr_patience=10, es_patience=20)
    
    
def optuna_create_evaluation_tilt(model):
    temp_yhat = model.predict(X_val['upac08'][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X',
                                               'Year Y', 'Year X']])
    return sklearn.metrics.mean_squared_error(y_val['upac08'], temp_yhat)
    
    
def objective_tilt(trial):
    # Instantiate the model
    temp_model = optuna_create_model_tilt(trial)
    
    # Train the model
    optuna_create_training_tilt(temp_model)
    
    # Evaluate model
    metrics_val = optuna_create_evaluation_tilt(temp_model)
    
    return metrics_val

study_tilt = optuna.create_study(direction='minimize')
study_tilt.optimize(objective_tilt, n_trials=100, show_progress_bar=True)

[I 2022-08-01 22:27:40,220] A new study created in memory with name: no-name-0460507d-985f-4b6d-b86e-ec24ca11d478
c:\users\feel\jupyter\ecgomes\upacs_study\venv\lib\site-packages\optuna\progress_bar.py:47: ExperimentalWarning: Progress bar is experimental (supported from v1.2.0). The interface can change in the future.
  self._init_valid()


  0%|          | 0/100 [00:00<?, ?it/s]

[TabNet]: 32 features will be used for decision steps.
Epoch 1/50
1089/1089 [==============================] - 3s 2ms/step - loss: 1641605.1250 - mae: 704.0300 - val_loss: 1258459.3750 - val_mae: 591.0825 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 2s 2ms/step - loss: 1314314.2500 - mae: 620.2015 - val_loss: 949937.3125 - val_mae: 519.8673 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 2ms/step - loss: 967126.3750 - mae: 538.1475 - val_loss: 721043.5625 - val_mae: 478.5097 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 2ms/step - loss: 733208.8750 - mae: 482.5236 - val_loss: 618818.9375 - val_mae: 468.3935 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 2ms/step - loss: 609681.0625 - mae: 452.7925 - val_loss: 596644.7500 - val_mae: 472.3998 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 2ms/step - loss: 557110.1875 - mae: 439.8972 - val_loss: 604097.3125 - val_mae

Epoch 7/50
1089/1089 [==============================] - 1s 979us/step - loss: 231884.0938 - mae: 242.9442 - val_loss: 182274.2812 - val_mae: 219.2136 - lr: 0.0010
Epoch 8/50
1089/1089 [==============================] - 1s 979us/step - loss: 170791.7812 - mae: 214.2983 - val_loss: 154891.2031 - val_mae: 197.4163 - lr: 0.0010
Epoch 9/50
1089/1089 [==============================] - 1s 976us/step - loss: 139145.9688 - mae: 194.8276 - val_loss: 137473.2500 - val_mae: 187.1414 - lr: 0.0010
Epoch 10/50
1089/1089 [==============================] - 1s 980us/step - loss: 125804.1797 - mae: 184.9951 - val_loss: 138560.4688 - val_mae: 181.8659 - lr: 0.0010
Epoch 11/50
1089/1089 [==============================] - 1s 976us/step - loss: 117059.6719 - mae: 175.9967 - val_loss: 130754.8281 - val_mae: 178.1259 - lr: 0.0010
Epoch 12/50
1089/1089 [==============================] - 1s 983us/step - loss: 112774.1094 - mae: 171.3332 - val_loss: 128117.7656 - val_mae: 169.7490 - lr: 0.0010
Epoch 13/50
1089/10

1089/1089 [==============================] - 2s 2ms/step - loss: 1305015.0000 - mae: 597.5999 - val_loss: 919231.2500 - val_mae: 465.4623 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 2ms/step - loss: 926137.6250 - mae: 485.3797 - val_loss: 628538.9375 - val_mae: 383.9536 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 2ms/step - loss: 632616.5000 - mae: 398.8915 - val_loss: 428118.3125 - val_mae: 318.5321 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 2ms/step - loss: 453224.4688 - mae: 345.7807 - val_loss: 357497.0625 - val_mae: 310.3549 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 2ms/step - loss: 356344.7188 - mae: 313.9553 - val_loss: 279823.9688 - val_mae: 255.9543 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 2s 2ms/step - loss: 303163.5938 - mae: 291.4040 - val_loss: 224081.0781 - val_mae: 239.7749 - lr: 0.0010
Epoch 8/50
1089/1089 [======================

...

1089/1089 [==============================] - 1s 1ms/step - loss: 102568.9219 - mae: 151.5794 - val_loss: 118661.3594 - val_mae: 156.7344 - lr: 0.0010
Epoch 26/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98981.6016 - mae: 147.0319 - val_loss: 115923.3125 - val_mae: 153.3652 - lr: 1.0000e-04
Epoch 27/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98778.6875 - mae: 146.4447 - val_loss: 116613.2109 - val_mae: 153.8224 - lr: 1.0000e-04
Epoch 28/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98771.6797 - mae: 146.2851 - val_loss: 117617.6484 - val_mae: 154.8974 - lr: 1.0000e-04
Epoch 29/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98782.6094 - mae: 146.2997 - val_loss: 115992.2266 - val_mae: 153.8204 - lr: 1.0000e-04
Epoch 30/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98549.8750 - mae: 146.2264 - val_loss: 118423.1172 - val_mae: 155.7766 - lr: 1.0000e-04
Epoch 31/50
1089/1089 [==

Epoch 28/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101691.5312 - mae: 151.4139 - val_loss: 128990.4609 - val_mae: 168.2614 - lr: 0.0010
Epoch 29/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101630.7656 - mae: 151.5413 - val_loss: 132485.6094 - val_mae: 168.2966 - lr: 0.0010
Epoch 30/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100979.1172 - mae: 150.5621 - val_loss: 133345.4844 - val_mae: 170.4054 - lr: 0.0010
Epoch 31/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101286.4609 - mae: 150.7379 - val_loss: 125139.0391 - val_mae: 162.8168 - lr: 0.0010
Epoch 32/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101015.8125 - mae: 150.6276 - val_loss: 124468.1172 - val_mae: 161.9923 - lr: 0.0010
Epoch 33/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100675.6719 - mae: 150.4772 - val_loss: 116482.3594 - val_mae: 156.2959 - lr: 0.0010
Epoch 34/50
1089/1089 [=====

Epoch 31/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97231.5000 - mae: 144.5262 - val_loss: 117712.3516 - val_mae: 155.9500 - lr: 1.0000e-04
Epoch 32/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97197.9141 - mae: 144.6313 - val_loss: 118075.7266 - val_mae: 155.9704 - lr: 1.0000e-04
Epoch 33/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97162.0859 - mae: 144.4435 - val_loss: 116625.7969 - val_mae: 154.1884 - lr: 1.0000e-04
Epoch 34/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97129.1562 - mae: 144.4102 - val_loss: 116531.6250 - val_mae: 154.7389 - lr: 1.0000e-04
Epoch 35/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97068.8047 - mae: 144.4747 - val_loss: 116031.7891 - val_mae: 153.7557 - lr: 1.0000e-04
[I 2022-08-02 00:30:55,488] Trial 95 finished with value: 116031.77873562474 and parameters: {'feature_dim': 51, 'output_dim': 11, 'num_decision_steps': 1}. Best is trial 85 w

1089/1089 [==============================] - 1s 1ms/step - loss: 97035.1172 - mae: 144.7213 - val_loss: 115043.3828 - val_mae: 152.8884 - lr: 1.0000e-04
Epoch 45/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97009.0859 - mae: 144.4831 - val_loss: 116660.9688 - val_mae: 154.1032 - lr: 1.0000e-04
Epoch 46/50
1089/1089 [==============================] - 1s 1ms/step - loss: 97040.2266 - mae: 144.7447 - val_loss: 116458.6406 - val_mae: 153.9038 - lr: 1.0000e-04
[I 2022-08-02 00:32:54,544] Trial 97 finished with value: 116458.63104737463 and parameters: {'feature_dim': 49, 'output_dim': 6, 'num_decision_steps': 1}. Best is trial 85 with value: 110364.09533551737.
Epoch 1/50
1089/1089 [==============================] - 2s 2ms/step - loss: 1626343.7500 - mae: 704.1471 - val_loss: 1230479.0000 - val_mae: 568.0603 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1268319.6250 - mae: 588.8547 - val_loss: 880785.6250 - val_mae: 455.5209 

1089/1089 [==============================] - 2s 1ms/step - loss: 1667015.2500 - mae: 719.5042 - val_loss: 1291752.5000 - val_mae: 589.1721 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1362222.2500 - mae: 618.6799 - val_loss: 978030.3125 - val_mae: 491.1794 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 988690.4375 - mae: 501.7343 - val_loss: 669077.6875 - val_mae: 385.0163 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 1s 1ms/step - loss: 662511.2500 - mae: 395.1829 - val_loss: 438445.7500 - val_mae: 307.8323 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 1s 1ms/step - loss: 426824.8125 - mae: 315.0949 - val_loss: 288531.0938 - val_mae: 254.5085 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 1s 1ms/step - loss: 276937.9375 - mae: 258.1113 - val_loss: 211696.5000 - val_mae: 220.6503 - lr: 0.0010
Epoch 7/50
1089/1089 [====================

In [46]:
# Aux Function for predicting and storing values

def do_predictions(dictionary, save_path, X, y, index):
    # Go through each model in the dictionary
    for model in dictionary.keys():
        print('Doing {}'.format(model))
        
        temp_path = '{}/{}.csv'.format(save_path, model)
        
        y_pred = dictionary[model].predict(X, verbose=1)
        y_pred = pd.DataFrame(y_pred[:, :], columns=['PV'],
                              index=index)
        
        y_pred.to_csv(temp_path)
        
    # Also save ground-truth data at the end of the loop
    y_true = pd.DataFrame(y, columns=['PV'],
                          index=index)
    
    temp_path_gt = '{}/gt.csv'.format(save_path)
    y_true.to_csv(temp_path_gt)
    
    
def predict_upacs_tilt(model_dictionary, upac_name, X_train, y_train, X_val, y_val, X_test, y_test):
    # Simply call the function above for each of the settings to simplify
    
    print('Doing training for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_gti/train'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_train[upac_name][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_train[upac_name],
                   index=normalized_train[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing validation for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_gti/val'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_val[upac_name][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_val[upac_name],
                   index=normalized_val[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing testing for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_gti/test'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_test[upac_name][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_test[upac_name],
                   index=normalized_test[upac_name].index)
    IPython.display.clear_output()

In [61]:
# Train 10 Models for UPAC08 - Gti

N_MODELS = 10
upac08_Gti = {}

for i in np.arange(N_MODELS):
    IPython.display.clear_output()
    print('Current Model: {:02d}'.format(i+1))
    
    tabnet_regressor = StackedTabNetRegressor(feature_columns=None,
                                              num_layers=1, #study.best_params['num_layers'],
                                              num_regressors=1, 
                                              feature_dim=study_tilt.best_params['feature_dim'],
                                              num_features=7, 
                                              output_dim=study_tilt.best_params['output_dim'],
                                              num_decision_steps=study_tilt.best_params['num_decision_steps'],
                                              num_groups=1)
    current_net_history = compile_and_fit(tabnet_regressor, 
                                          X_train['upac08'][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X',
                                                             'Year Y', 'Year X']], y_train['upac08'],
                                          X_val['upac08'][['AirTemp', 'CloudOpacity', 'GtiFixedTilt', 'Day Y', 'Day X',
                                                           'Year Y', 'Year X']], y_val['upac08'])
    
    tabnet_regressor.save('models/tabnet/upac08_gti/Model {:02d}'.format(i+1), save_format='tf')
    upac08_Gti['Model {:02d}'.format(i+1)] = tabnet_regressor

Current Model: 10
Epoch 1/1000
1089/1089 [==============================] - 3s 2ms/step - loss: 1638835.7500 - mae: 709.1601 - val_loss: 1247128.8750 - val_mae: 577.3998 - lr: 0.0010
Epoch 2/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 1287929.3750 - mae: 594.9966 - val_loss: 897182.3125 - val_mae: 461.0364 - lr: 0.0010
Epoch 3/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 886220.9375 - mae: 469.5598 - val_loss: 582315.3125 - val_mae: 359.1335 - lr: 0.0010
Epoch 4/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 561748.5000 - mae: 364.0316 - val_loss: 365421.8125 - val_mae: 289.0119 - lr: 0.0010
Epoch 5/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 345049.3750 - mae: 287.2331 - val_loss: 243241.5156 - val_mae: 240.1706 - lr: 0.0010
Epoch 6/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 221754.1250 - mae: 234.7167 - val_loss: 189961.6094 - val_mae: 213.0340 - lr: 0.0010
E

1089/1089 [==============================] - 2s 2ms/step - loss: 97272.6797 - mae: 145.7383 - val_loss: 112996.9062 - val_mae: 151.5185 - lr: 0.0010
Epoch 52/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 96615.5547 - mae: 144.9104 - val_loss: 113599.5703 - val_mae: 152.2091 - lr: 0.0010
Epoch 53/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 96636.8906 - mae: 144.6557 - val_loss: 109877.9297 - val_mae: 149.1900 - lr: 0.0010
Epoch 54/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 96928.3125 - mae: 145.2856 - val_loss: 113111.6797 - val_mae: 151.7193 - lr: 0.0010
Epoch 55/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 96378.4609 - mae: 144.9117 - val_loss: 113056.3281 - val_mae: 150.3897 - lr: 0.0010
Epoch 56/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 96328.3047 - mae: 144.7204 - val_loss: 117417.0000 - val_mae: 157.3971 - lr: 0.0010
Epoch 57/1000
1089/1089 [===========

Epoch 151/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81891.2266 - mae: 130.1437 - val_loss: 117201.1406 - val_mae: 152.6436 - lr: 1.0000e-04
Epoch 152/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81838.0312 - mae: 129.9716 - val_loss: 117297.7031 - val_mae: 151.9417 - lr: 1.0000e-04
Epoch 153/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81649.6172 - mae: 130.0704 - val_loss: 118337.8594 - val_mae: 152.9222 - lr: 1.0000e-04
Epoch 154/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81705.6875 - mae: 130.0501 - val_loss: 117617.1328 - val_mae: 152.2745 - lr: 1.0000e-04
Epoch 155/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81586.5469 - mae: 129.9172 - val_loss: 117739.6172 - val_mae: 152.6591 - lr: 1.0000e-04
Epoch 156/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 81571.7500 - mae: 129.9216 - val_loss: 117951.1641 - val_mae: 152.4052 - lr: 1.0

Epoch 200/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79426.8438 - mae: 128.2151 - val_loss: 120359.2891 - val_mae: 154.5227 - lr: 1.0000e-04
Epoch 201/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79455.5625 - mae: 128.2863 - val_loss: 120603.5781 - val_mae: 155.1179 - lr: 1.0000e-04
Epoch 202/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79438.3672 - mae: 128.3246 - val_loss: 120614.8203 - val_mae: 154.1799 - lr: 1.0000e-04
Epoch 203/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79298.6875 - mae: 128.2358 - val_loss: 121632.6094 - val_mae: 154.7554 - lr: 1.0000e-04
Epoch 204/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79362.7109 - mae: 127.9505 - val_loss: 120311.7188 - val_mae: 154.5016 - lr: 1.0000e-04
Epoch 205/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 79244.7578 - mae: 128.1789 - val_loss: 120521.2656 - val_mae: 154.6537 - lr: 1.0

In [62]:
# UPAC08 Predictions for GtiFixedTilt

predict_upacs_tilt(model_dictionary=upac08_Gti, 
                   upac_name='upac08',
                   X_train=X_train, y_train=y_train,
                   X_val=X_val, y_val=y_val,
                   X_test=X_test, y_test=y_test)

#############################

In [63]:
# Optuna for TabNet hyperparameter optimization - Ghi

import optuna
import sklearn

import random

random.seed(69)
np.random.seed(69)
tf.random.set_seed(69)

def optuna_create_model_ghi(trial):
    # Do search for n_estimators, max_depth, reg_alpha and reg_lambda
    #sug_layers = trial.suggest_int('num_layers', 1, 4)
    sug_fdim = trial.suggest_int('feature_dim', 32, 72)
    sug_odim = trial.suggest_int('output_dim', 4, 12)
    sug_dsteps = trial.suggest_int('num_decision_steps', 1, 4)
    
    sug_model = StackedTabNetRegressor(feature_columns=None,
                                       num_layers=1, #sug_layers,
                                       num_regressors=1, 
                                       feature_dim=sug_fdim,
                                       num_features=7, 
                                       output_dim=sug_odim,
                                       num_decision_steps=sug_dsteps,
                                       num_groups=1)
    
    return sug_model


def optuna_create_training_ghi(model):
    compile_and_fit(model, X_train['upac08'].drop('Ghi', axis=1), y_train['upac08'],
                    X_val['upac08'].drop('Ghi', axis=1), y_val['upac08'],
                    max_epochs=50, rlr_patience=10, es_patience=20)
    
    
def optuna_create_evaluation_ghi(model):
    temp_yhat = model.predict(X_val['upac08'].drop('Ghi', axis=1))
    return sklearn.metrics.mean_squared_error(y_val['upac08'], temp_yhat)
    
    
def objective_ghi(trial):
    # Instantiate the model
    temp_model = optuna_create_model_ghi(trial)
    
    # Train the model
    optuna_create_training_ghi(temp_model)
    
    # Evaluate model
    metrics_val = optuna_create_evaluation_ghi(temp_model)
    
    return metrics_val

study_ghi = optuna.create_study(direction='minimize')
study_ghi.optimize(objective_ghi, n_trials=100, show_progress_bar=True)

[I 2022-08-04 03:36:49,707] A new study created in memory with name: no-name-6038244f-5fca-4a90-8609-bf99e0ba6a2b
c:\users\feel\jupyter\ecgomes\upacs_study\venv\lib\site-packages\optuna\progress_bar.py:47: ExperimentalWarning: Progress bar is experimental (supported from v1.2.0). The interface can change in the future.
  self._init_valid()


  0%|          | 0/100 [00:00<?, ?it/s]

[TabNet]: 25 features will be used for decision steps.
Epoch 1/50
1089/1089 [==============================] - 6s 3ms/step - loss: 1544043.6250 - mae: 716.0977 - val_loss: 1052478.5000 - val_mae: 621.0658 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 3s 3ms/step - loss: 1004049.1875 - mae: 664.0312 - val_loss: 673952.6875 - val_mae: 586.3903 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 3s 3ms/step - loss: 665294.5000 - mae: 572.6391 - val_loss: 387293.4688 - val_mae: 322.0149 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 3s 3ms/step - loss: 354628.6250 - mae: 322.6206 - val_loss: 230455.7344 - val_mae: 254.3921 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 3s 3ms/step - loss: 239207.7188 - mae: 267.9255 - val_loss: 198604.6250 - val_mae: 229.8379 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 3s 3ms/step - loss: 195068.7344 - mae: 244.5269 - val_loss: 186166.0625 - val_mae

1089/1089 [==============================] - 5s 3ms/step - loss: 1584066.0000 - mae: 707.3925 - val_loss: 1111781.3750 - val_mae: 597.2832 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 2s 2ms/step - loss: 1075753.2500 - mae: 606.0186 - val_loss: 736291.6250 - val_mae: 538.8325 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 2ms/step - loss: 731127.0625 - mae: 525.3698 - val_loss: 637851.8750 - val_mae: 524.3618 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 2ms/step - loss: 613963.8125 - mae: 479.4638 - val_loss: 594909.5625 - val_mae: 498.0808 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 2ms/step - loss: 604008.0000 - mae: 478.4827 - val_loss: 630100.1875 - val_mae: 507.7646 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 2ms/step - loss: 576536.8125 - mae: 467.1545 - val_loss: 626232.9375 - val_mae: 511.0427 - lr: 0.0010
Epoch 7/50
1089/1089 [====================

[I 2022-08-04 03:41:40,472] Trial 1 finished with value: 500867.72647886333 and parameters: {'feature_dim': 33, 'output_dim': 12, 'num_decision_steps': 3}. Best is trial 0 with value: 166442.36637098403.
[TabNet]: 42 features will be used for decision steps.
Epoch 1/50
1089/1089 [==============================] - 5s 3ms/step - loss: 1581722.6250 - mae: 683.7264 - val_loss: 1133467.6250 - val_mae: 536.5084 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 3s 3ms/step - loss: 1084301.6250 - mae: 537.7648 - val_loss: 677936.6250 - val_mae: 398.1253 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 3s 3ms/step - loss: 640300.6875 - mae: 409.9154 - val_loss: 396166.6562 - val_mae: 319.2755 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 3s 3ms/step - loss: 437686.4062 - mae: 360.9907 - val_loss: 433460.5312 - val_mae: 374.2029 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 3s 3ms/step - loss: 332836.0000 - mae:

...

1089/1089 [==============================] - 2s 2ms/step - loss: 349161.2812 - mae: 287.0338 - val_loss: 240567.7500 - val_mae: 237.0081 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 2ms/step - loss: 223618.2031 - mae: 234.9922 - val_loss: 183361.0781 - val_mae: 206.1099 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 2s 2ms/step - loss: 161091.3750 - mae: 203.0459 - val_loss: 147039.9219 - val_mae: 187.1246 - lr: 0.0010
Epoch 8/50
1089/1089 [==============================] - 2s 2ms/step - loss: 132960.2656 - mae: 184.9347 - val_loss: 135053.8906 - val_mae: 173.1765 - lr: 0.0010
Epoch 9/50
1089/1089 [==============================] - 2s 2ms/step - loss: 120167.1016 - mae: 174.6263 - val_loss: 126419.0234 - val_mae: 170.4544 - lr: 0.0010
Epoch 10/50
1089/1089 [==============================] - 2s 2ms/step - loss: 113304.7422 - mae: 167.3844 - val_loss: 135154.2344 - val_mae: 174.3385 - lr: 0.0010
Epoch 11/50
1089/1089 [=====================

1089/1089 [==============================] - 2s 1ms/step - loss: 1081191.6250 - mae: 528.7401 - val_loss: 757927.3750 - val_mae: 412.4674 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 2ms/step - loss: 771019.0000 - mae: 429.7544 - val_loss: 526048.5625 - val_mae: 339.8267 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 2ms/step - loss: 524878.8750 - mae: 348.6571 - val_loss: 357332.5312 - val_mae: 282.7819 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 1ms/step - loss: 351726.4688 - mae: 287.3781 - val_loss: 262951.0625 - val_mae: 245.3972 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 2s 1ms/step - loss: 241306.4688 - mae: 242.8403 - val_loss: 190629.3125 - val_mae: 212.9557 - lr: 0.0010
Epoch 8/50
1089/1089 [==============================] - 2s 1ms/step - loss: 177357.0938 - mae: 212.0723 - val_loss: 160098.6250 - val_mae: 193.1065 - lr: 0.0010
Epoch 9/50
1089/1089 [======================

1089/1089 [==============================] - 2s 2ms/step - loss: 1762661.1250 - mae: 737.2346 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1762661.7500 - mae: 737.2341 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1762661.0000 - mae: 737.2339 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1762660.2500 - mae: 737.2343 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1762661.1250 - mae: 737.2339 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1762661.2500 - mae: 737.2347 - val_loss: 1487782.3750 - val_mae: 647.6166 - lr: 0.0010
Epoch 7/50
1089/1089 [===========

Epoch 29/50
1089/1089 [==============================] - 2s 1ms/step - loss: 98383.5781 - mae: 145.5320 - val_loss: 114813.4531 - val_mae: 151.9429 - lr: 1.0000e-04
Epoch 30/50
1089/1089 [==============================] - 2s 1ms/step - loss: 98216.9844 - mae: 145.5525 - val_loss: 116966.9609 - val_mae: 154.2054 - lr: 1.0000e-04
Epoch 31/50
1089/1089 [==============================] - 2s 1ms/step - loss: 98260.3672 - mae: 145.3706 - val_loss: 117563.1172 - val_mae: 154.6066 - lr: 1.0000e-04
Epoch 32/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98282.0859 - mae: 145.4717 - val_loss: 118256.4297 - val_mae: 154.6728 - lr: 1.0000e-04
Epoch 33/50
1089/1089 [==============================] - 1s 1ms/step - loss: 98166.8203 - mae: 145.2886 - val_loss: 115671.6797 - val_mae: 152.2693 - lr: 1.0000e-04
Epoch 34/50
1089/1089 [==============================] - 2s 1ms/step - loss: 98161.9297 - mae: 145.1182 - val_loss: 116878.3594 - val_mae: 153.5858 - lr: 1.0000e-04
Epoch 35/5

Epoch 32/50
1089/1089 [==============================] - 1s 1ms/step - loss: 101117.5391 - mae: 151.4863 - val_loss: 128575.3516 - val_mae: 166.7553 - lr: 0.0010
Epoch 33/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100750.2188 - mae: 151.5351 - val_loss: 119970.7656 - val_mae: 159.6213 - lr: 0.0010
Epoch 34/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100641.6875 - mae: 150.6414 - val_loss: 120111.2969 - val_mae: 161.2289 - lr: 0.0010
Epoch 35/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100525.8438 - mae: 150.3392 - val_loss: 119122.9297 - val_mae: 160.9907 - lr: 0.0010
Epoch 36/50
1089/1089 [==============================] - 1s 1ms/step - loss: 100074.7500 - mae: 149.8176 - val_loss: 117449.1094 - val_mae: 159.0369 - lr: 0.0010
Epoch 37/50
1089/1089 [==============================] - 1s 1ms/step - loss: 99996.9219 - mae: 149.5685 - val_loss: 118775.1484 - val_mae: 159.1420 - lr: 0.0010
Epoch 38/50
1089/1089 [======

In [64]:
# Aux Function for predicting and storing values

def do_predictions(dictionary, save_path, X, y, index):
    # Go through each model in the dictionary
    for model in dictionary.keys():
        print('Doing {}'.format(model))
        
        temp_path = '{}/{}.csv'.format(save_path, model)
        
        y_pred = dictionary[model].predict(X, verbose=1)
        y_pred = pd.DataFrame(y_pred[:, :], columns=['PV'],
                              index=index)
        
        y_pred.to_csv(temp_path)
        
    # Also save ground-truth data at the end of the loop
    y_true = pd.DataFrame(y, columns=['PV'],
                          index=index)
    
    temp_path_gt = '{}/gt.csv'.format(save_path)
    y_true.to_csv(temp_path_gt)
    
    
def predict_upacs_ghi(model_dictionary, upac_name, X_train, y_train, X_val, y_val, X_test, y_test):
    # Simply call the function above for each of the settings to simplify
    
    print('Doing training for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi/train'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_train[upac_name][['AirTemp', 'CloudOpacity', 'Ghi', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_train[upac_name],
                   index=normalized_train[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing validation for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi/val'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_val[upac_name][['AirTemp', 'CloudOpacity', 'Ghi', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_val[upac_name],
                   index=normalized_val[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing testing for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_ghi/test'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_test[upac_name][['AirTemp', 'CloudOpacity', 'Ghi', 'Day Y', 'Day X', 'Year Y', 'Year X']], 
                   y=y_test[upac_name],
                   index=normalized_test[upac_name].index)
    IPython.display.clear_output()

In [65]:
# Train 10 Models for UPAC08 - Gti

N_MODELS = 10
upac08_Ghi = {}

for i in np.arange(N_MODELS):
    IPython.display.clear_output()
    print('Current Model: {:02d}'.format(i+1))
    
    tabnet_regressor = StackedTabNetRegressor(feature_columns=None,
                                              num_layers=1, #study.best_params['num_layers'],
                                              num_regressors=1, 
                                              feature_dim=study_ghi.best_params['feature_dim'],
                                              num_features=7, 
                                              output_dim=study_ghi.best_params['output_dim'],
                                              num_decision_steps=study_ghi.best_params['num_decision_steps'],
                                              num_groups=1)
    current_net_history = compile_and_fit(tabnet_regressor, 
                                          X_train['upac08'][['AirTemp', 'CloudOpacity', 'Ghi', 'Day Y', 'Day X',
                                                             'Year Y', 'Year X']], y_train['upac08'],
                                          X_val['upac08'][['AirTemp', 'CloudOpacity', 'Ghi', 'Day Y', 'Day X',
                                                           'Year Y', 'Year X']], y_val['upac08'])
    
    tabnet_regressor.save('models/tabnet/upac08_ghi/Model {:02d}'.format(i+1), save_format='tf')
    upac08_Ghi['Model {:02d}'.format(i+1)] = tabnet_regressor

Current Model: 10
Epoch 1/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 1670649.7500 - mae: 720.6699 - val_loss: 1305891.2500 - val_mae: 594.5675 - lr: 0.0010
Epoch 2/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 1401966.3750 - mae: 631.4655 - val_loss: 1032333.6250 - val_mae: 505.9269 - lr: 0.0010
Epoch 3/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 1070885.2500 - mae: 528.1787 - val_loss: 747717.9375 - val_mae: 410.1213 - lr: 0.0010
Epoch 4/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 762437.9375 - mae: 429.6940 - val_loss: 514581.8750 - val_mae: 334.9062 - lr: 0.0010
Epoch 5/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 516813.3438 - mae: 347.8554 - val_loss: 348790.5938 - val_mae: 277.0005 - lr: 0.0010
Epoch 6/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 343873.8125 - mae: 285.1868 - val_loss: 246293.0625 - val_mae: 236.2695 - lr: 0.0010

Epoch 51/1000
1089/1089 [==============================] - 2s 1ms/step - loss: 98731.2500 - mae: 146.7593 - val_loss: 111748.3594 - val_mae: 148.5196 - lr: 0.0010
Epoch 52/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 98263.7656 - mae: 145.8210 - val_loss: 113334.1641 - val_mae: 150.6406 - lr: 0.0010
Epoch 53/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 97966.9922 - mae: 145.6064 - val_loss: 110074.6953 - val_mae: 148.0819 - lr: 0.0010
Epoch 54/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 98187.9766 - mae: 145.6988 - val_loss: 110033.9766 - val_mae: 147.6332 - lr: 0.0010
Epoch 55/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 98007.3828 - mae: 145.8689 - val_loss: 113517.0781 - val_mae: 152.0040 - lr: 0.0010
Epoch 56/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 97999.4766 - mae: 145.9040 - val_loss: 114023.8359 - val_mae: 152.3210 - lr: 0.0010
Epoch 57/1000
1089/108

1089/1089 [==============================] - 2s 2ms/step - loss: 87898.5781 - mae: 135.7867 - val_loss: 117637.1719 - val_mae: 154.3900 - lr: 0.0010
Epoch 152/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 87686.3516 - mae: 135.7540 - val_loss: 121434.6641 - val_mae: 156.3533 - lr: 0.0010
Epoch 153/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 87602.3828 - mae: 135.6046 - val_loss: 119928.6406 - val_mae: 158.4489 - lr: 0.0010
Epoch 154/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 87929.0312 - mae: 136.1354 - val_loss: 120307.2734 - val_mae: 156.9285 - lr: 0.0010
Epoch 155/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 87249.8516 - mae: 135.7297 - val_loss: 122924.4297 - val_mae: 159.5676 - lr: 0.0010
Epoch 156/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 87933.2891 - mae: 135.9746 - val_loss: 119674.1406 - val_mae: 155.1506 - lr: 0.0010
Epoch 157/1000
1089/1089 [=====

Epoch 201/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76862.2969 - mae: 125.5270 - val_loss: 124026.3594 - val_mae: 157.1612 - lr: 1.0000e-04
Epoch 202/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76927.1641 - mae: 125.7068 - val_loss: 123241.7656 - val_mae: 156.3436 - lr: 1.0000e-04
Epoch 203/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76800.1953 - mae: 125.4276 - val_loss: 124639.2891 - val_mae: 157.7146 - lr: 1.0000e-04
Epoch 204/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76725.2109 - mae: 125.4344 - val_loss: 125011.8047 - val_mae: 158.1917 - lr: 1.0000e-04
Epoch 205/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76655.4531 - mae: 125.3274 - val_loss: 124795.5000 - val_mae: 157.8965 - lr: 1.0000e-04
Epoch 206/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 76624.9844 - mae: 125.3868 - val_loss: 124329.1094 - val_mae: 157.3910 - lr: 1.0

Epoch 250/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74363.7344 - mae: 123.9886 - val_loss: 130269.2578 - val_mae: 161.0436 - lr: 1.0000e-04
Epoch 251/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74457.3125 - mae: 123.9152 - val_loss: 129616.2656 - val_mae: 160.9800 - lr: 1.0000e-04
Epoch 252/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74333.7656 - mae: 123.9621 - val_loss: 129678.2656 - val_mae: 160.4671 - lr: 1.0000e-04
Epoch 253/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74227.1406 - mae: 123.7346 - val_loss: 129062.2969 - val_mae: 160.2177 - lr: 1.0000e-04
Epoch 254/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74195.6484 - mae: 123.8153 - val_loss: 128993.2734 - val_mae: 159.9781 - lr: 1.0000e-04
Epoch 255/1000
1089/1089 [==============================] - 2s 2ms/step - loss: 74148.3594 - mae: 123.7458 - val_loss: 129527.7188 - val_mae: 161.1735 - lr: 1.0

In [66]:
# UPAC08 Predictions for Ghi

predict_upacs_ghi(model_dictionary=upac08_Ghi, 
                   upac_name='upac08',
                   X_train=X_train, y_train=y_train,
                   X_val=X_val, y_val=y_val,
                   X_test=X_test, y_test=y_test)

###########################

In [49]:
# Optuna for TabNet hyperparameter optimization - Day X and Ghi

import optuna
import sklearn

import random

random.seed(69)
np.random.seed(69)
tf.random.set_seed(69)

def optuna_create_model_top2(trial):
    # Do search for n_estimators, max_depth, reg_alpha and reg_lambda
    #sug_layers = trial.suggest_int('num_layers', 1, 4)
    sug_fdim = trial.suggest_int('feature_dim', 32, 72)
    sug_odim = trial.suggest_int('output_dim', 4, 12)
    sug_dsteps = trial.suggest_int('num_decision_steps', 1, 4)
    
    sug_model = StackedTabNetRegressor(feature_columns=None,
                                       num_layers=1, #sug_layers,
                                       num_regressors=1, 
                                       feature_dim=sug_fdim,
                                       num_features=2, 
                                       output_dim=sug_odim,
                                       num_decision_steps=sug_dsteps,
                                       num_groups=1)
    
    return sug_model


def optuna_create_training_top2(model):
    compile_and_fit(model, 
                    X_train['upac08'][['Ghi', 'Day X']], y_train['upac08'],
                    X_val['upac08'][['Ghi', 'Day X']], y_val['upac08'],
                    max_epochs=50, rlr_patience=10, es_patience=20)
    
    
def optuna_create_evaluation_top2(model):
    temp_yhat = model.predict(X_val['upac08'][['Ghi', 'Day X']])
    return sklearn.metrics.mean_squared_error(y_val['upac08'], temp_yhat)
    
    
def objective_top2(trial):
    # Instantiate the model
    temp_model = optuna_create_model_top2(trial)
    
    # Train the model
    optuna_create_training_top2(temp_model)
    
    # Evaluate model
    metrics_val = optuna_create_evaluation_top2(temp_model)
    
    return metrics_val

study_top2 = optuna.create_study(direction='minimize')
study_top2.optimize(objective_top2, n_trials=100, show_progress_bar=True)

[I 2022-08-02 04:14:38,301] A new study created in memory with name: no-name-8d3ead74-cc98-432b-ad0d-6d028087b69e
c:\users\feel\jupyter\ecgomes\upacs_study\venv\lib\site-packages\optuna\progress_bar.py:47: ExperimentalWarning: Progress bar is experimental (supported from v1.2.0). The interface can change in the future.
  self._init_valid()


  0%|          | 0/100 [00:00<?, ?it/s]

Epoch 1/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1639471.5000 - mae: 702.1213 - val_loss: 1236367.2500 - val_mae: 581.5900 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1251642.7500 - mae: 583.6678 - val_loss: 852468.0000 - val_mae: 445.9172 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 837865.7500 - mae: 463.1636 - val_loss: 557184.2500 - val_mae: 357.4144 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 1s 1ms/step - loss: 567953.3750 - mae: 389.0113 - val_loss: 362178.8750 - val_mae: 297.6066 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 1s 1ms/step - loss: 408572.4062 - mae: 336.3800 - val_loss: 267185.9375 - val_mae: 253.5846 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 1s 1ms/step - loss: 322924.8125 - mae: 304.2752 - val_loss: 214313.9062 - val_mae: 232.0849 - lr: 0.0010
Epoch 7/50
1089/1089 [=========

Epoch 10/50
1089/1089 [==============================] - 4s 4ms/step - loss: 210774.7656 - mae: 260.8968 - val_loss: 205695.0156 - val_mae: 239.7493 - lr: 0.0010
Epoch 11/50
1089/1089 [==============================] - 4s 3ms/step - loss: 204119.6094 - mae: 254.5253 - val_loss: 236345.9844 - val_mae: 253.9645 - lr: 0.0010
Epoch 12/50
1089/1089 [==============================] - 4s 3ms/step - loss: 201981.1562 - mae: 250.7360 - val_loss: 203782.6562 - val_mae: 232.4693 - lr: 0.0010
Epoch 13/50
1089/1089 [==============================] - 4s 3ms/step - loss: 199723.2031 - mae: 247.2725 - val_loss: 196353.9219 - val_mae: 229.8527 - lr: 0.0010
Epoch 14/50
1089/1089 [==============================] - 4s 3ms/step - loss: 199318.7656 - mae: 246.2179 - val_loss: 176330.1094 - val_mae: 216.0982 - lr: 0.0010
Epoch 15/50
1089/1089 [==============================] - 4s 3ms/step - loss: 197572.2969 - mae: 243.8249 - val_loss: 199868.3438 - val_mae: 225.7025 - lr: 0.0010
Epoch 16/50
1089/1089 [=====

Epoch 18/50
1089/1089 [==============================] - 4s 4ms/step - loss: 198902.0781 - mae: 240.3087 - val_loss: 162262.7031 - val_mae: 200.0927 - lr: 0.0010
Epoch 19/50
1089/1089 [==============================] - 4s 4ms/step - loss: 189113.1250 - mae: 234.9941 - val_loss: 199333.1562 - val_mae: 220.4148 - lr: 1.0000e-04
Epoch 20/50
1089/1089 [==============================] - 4s 4ms/step - loss: 191617.0000 - mae: 235.5162 - val_loss: 213858.7656 - val_mae: 231.6220 - lr: 1.0000e-04
Epoch 21/50
1089/1089 [==============================] - 4s 4ms/step - loss: 190515.0469 - mae: 238.0019 - val_loss: 169185.7969 - val_mae: 207.3799 - lr: 1.0000e-04
Epoch 22/50
1089/1089 [==============================] - 4s 4ms/step - loss: 188395.1250 - mae: 235.9863 - val_loss: 196830.3281 - val_mae: 221.9229 - lr: 1.0000e-04
Epoch 23/50
1089/1089 [==============================] - 4s 4ms/step - loss: 187948.7812 - mae: 235.2494 - val_loss: 196316.3281 - val_mae: 221.1734 - lr: 1.0000e-04
Epoch 24

...

Epoch 25/50
1089/1089 [==============================] - 2s 2ms/step - loss: 197327.3594 - mae: 238.7616 - val_loss: 219085.2188 - val_mae: 229.2641 - lr: 0.0010
Epoch 26/50
1089/1089 [==============================] - 2s 2ms/step - loss: 196528.8594 - mae: 238.7718 - val_loss: 198063.4531 - val_mae: 218.3118 - lr: 0.0010
Epoch 27/50
1089/1089 [==============================] - 2s 2ms/step - loss: 196691.5312 - mae: 238.5244 - val_loss: 196462.9531 - val_mae: 217.5918 - lr: 0.0010
Epoch 28/50
1089/1089 [==============================] - 2s 2ms/step - loss: 194019.2500 - mae: 237.2075 - val_loss: 185562.0000 - val_mae: 213.1359 - lr: 0.0010
Epoch 29/50
1089/1089 [==============================] - 2s 2ms/step - loss: 188576.2500 - mae: 233.3206 - val_loss: 198675.2969 - val_mae: 218.4255 - lr: 1.0000e-04
Epoch 30/50
1089/1089 [==============================] - 2s 2ms/step - loss: 188043.5156 - mae: 233.0647 - val_loss: 200124.0781 - val_mae: 219.1135 - lr: 1.0000e-04
Epoch 31/50
1089/108

Epoch 2/50
1089/1089 [==============================] - 2s 2ms/step - loss: 1360746.1250 - mae: 614.6627 - val_loss: 978351.9375 - val_mae: 482.7176 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 2ms/step - loss: 998173.5000 - mae: 505.8272 - val_loss: 681778.5000 - val_mae: 387.9531 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 2ms/step - loss: 698611.6875 - mae: 416.9803 - val_loss: 471891.5000 - val_mae: 327.7153 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 2ms/step - loss: 506294.7812 - mae: 363.9370 - val_loss: 350721.0938 - val_mae: 280.2402 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 2ms/step - loss: 379122.4062 - mae: 320.2270 - val_loss: 255373.1250 - val_mae: 247.8127 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 2s 2ms/step - loss: 320878.3438 - mae: 302.4019 - val_loss: 217197.0938 - val_mae: 230.0624 - lr: 0.0010
Epoch 8/50
1089/1089 [===========

Epoch 13/50
1089/1089 [==============================] - 2s 2ms/step - loss: 217142.3125 - mae: 252.4322 - val_loss: 193503.3281 - val_mae: 215.2561 - lr: 0.0010
Epoch 14/50
1089/1089 [==============================] - 2s 2ms/step - loss: 211375.1875 - mae: 249.2062 - val_loss: 183851.8594 - val_mae: 211.2357 - lr: 0.0010
Epoch 15/50
1089/1089 [==============================] - 2s 2ms/step - loss: 203310.4531 - mae: 243.8814 - val_loss: 199009.8281 - val_mae: 219.1011 - lr: 0.0010
Epoch 16/50
1089/1089 [==============================] - 2s 2ms/step - loss: 200121.1562 - mae: 241.4400 - val_loss: 212049.0000 - val_mae: 224.2012 - lr: 0.0010
Epoch 17/50
1089/1089 [==============================] - 2s 2ms/step - loss: 197927.9531 - mae: 239.6930 - val_loss: 223266.3438 - val_mae: 231.4067 - lr: 0.0010
Epoch 18/50
1089/1089 [==============================] - 2s 2ms/step - loss: 197926.4062 - mae: 239.6767 - val_loss: 180892.5156 - val_mae: 208.1109 - lr: 0.0010
Epoch 19/50
1089/1089 [=====

Epoch 21/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469895.8125 - mae: 410.1714 - val_loss: 552377.5625 - val_mae: 459.0135 - lr: 1.0000e-04
Epoch 22/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469701.0625 - mae: 410.3607 - val_loss: 551202.0625 - val_mae: 458.5955 - lr: 1.0000e-04
Epoch 23/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469274.7500 - mae: 410.3680 - val_loss: 550149.1250 - val_mae: 457.4605 - lr: 1.0000e-04
Epoch 24/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469084.6250 - mae: 409.9852 - val_loss: 550053.1250 - val_mae: 457.6798 - lr: 1.0000e-04
Epoch 25/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469325.4062 - mae: 410.0971 - val_loss: 557351.7500 - val_mae: 461.9732 - lr: 1.0000e-04
Epoch 26/50
1089/1089 [==============================] - 3s 2ms/step - loss: 469105.6562 - mae: 410.0227 - val_loss: 557737.3125 - val_mae: 462.8303 - lr: 1.0000e-04
Epoc

Epoch 9/50
1089/1089 [==============================] - 2s 2ms/step - loss: 504228.7812 - mae: 423.1714 - val_loss: 589880.5625 - val_mae: 476.8827 - lr: 0.0010
Epoch 10/50
1089/1089 [==============================] - 2s 2ms/step - loss: 494498.6875 - mae: 420.3752 - val_loss: 556339.0000 - val_mae: 460.4135 - lr: 0.0010
Epoch 11/50
1089/1089 [==============================] - 2s 2ms/step - loss: 490545.5312 - mae: 418.3708 - val_loss: 595672.3125 - val_mae: 475.7443 - lr: 0.0010
Epoch 12/50
1089/1089 [==============================] - 2s 2ms/step - loss: 488118.9688 - mae: 417.1960 - val_loss: 539288.7500 - val_mae: 444.6162 - lr: 0.0010
Epoch 13/50
1089/1089 [==============================] - 2s 2ms/step - loss: 486839.8750 - mae: 416.7090 - val_loss: 528471.5000 - val_mae: 439.9996 - lr: 0.0010
Epoch 14/50
1089/1089 [==============================] - 3s 2ms/step - loss: 485004.1562 - mae: 415.5391 - val_loss: 547401.3750 - val_mae: 454.7142 - lr: 0.0010
Epoch 15/50
1089/1089 [======

In [57]:
# Aux Function for predicting and storing values

def do_predictions(dictionary, save_path, X, y, index):
    # Go through each model in the dictionary
    for model in dictionary.keys():
        print('Doing {}'.format(model))
        
        temp_path = '{}/{}.csv'.format(save_path, model)
        
        y_pred = dictionary[model].predict(X, verbose=1)
        y_pred = pd.DataFrame(y_pred[:, :], columns=['PV'],
                              index=index)
        
        y_pred.to_csv(temp_path)
        
    # Also save ground-truth data at the end of the loop
    y_true = pd.DataFrame(y, columns=['PV'],
                          index=index)
    
    temp_path_gt = '{}/gt.csv'.format(save_path)
    y_true.to_csv(temp_path_gt)
    
    
def predict_upacs_top2(model_dictionary, upac_name, X_train, y_train, X_val, y_val, X_test, y_test):
    # Simply call the function above for each of the settings to simplify
    
    print('Doing training for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_top2/train'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_train[upac_name][['Ghi', 'Day X']], 
                   y=y_train[upac_name],
                   index=normalized_train[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing validation for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_top2/val'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_val[upac_name][['Ghi', 'Day X']], 
                   y=y_val[upac_name],
                   index=normalized_val[upac_name].index)
    IPython.display.clear_output()
    
    print('Doing testing for {}'.format(upac_name))
    temp_path = 'results/tabnet/{}_top2/test'.format(upac_name)
    do_predictions(dictionary=model_dictionary, 
                   save_path=temp_path, 
                   X=X_test[upac_name][['Ghi', 'Day X']], 
                   y=y_test[upac_name],
                   index=normalized_test[upac_name].index)
    IPython.display.clear_output()

In [55]:
# Train 10 Models for UPAC08 - top2

N_MODELS = 10
upac08_top2 = {}

for i in np.arange(N_MODELS):
    IPython.display.clear_output()
    print('Current Model: {:02d}'.format(i+1))
    
    tabnet_regressor = StackedTabNetRegressor(feature_columns=None,
                                              num_layers=1, #study.best_params['num_layers'],
                                              num_regressors=1, 
                                              feature_dim=study_top2.best_params['feature_dim'],
                                              num_features=2, 
                                              output_dim=study_top2.best_params['output_dim'],
                                              num_decision_steps=study_top2.best_params['num_decision_steps'],
                                              num_groups=1)
    current_net_history = compile_and_fit(tabnet_regressor, 
                                          X_train['upac08'][['Ghi', 'Day X']], y_train['upac08'],
                                          X_val['upac08'][['Ghi', 'Day X']], y_val['upac08'])
    
    tabnet_regressor.save('models/tabnet/upac08_top2/Model {:02d}'.format(i+1), save_format='tf')
    upac08_top2['Model {:02d}'.format(i+1)] = tabnet_regressor

Current Model: 10
Epoch 1/1000
1089/1089 [==============================] - 3s 1ms/step - loss: 1686440.7500 - mae: 715.0847 - val_loss: 1338215.3750 - val_mae: 607.7010 - lr: 0.0010
Epoch 2/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 1455924.0000 - mae: 647.3315 - val_loss: 1091396.0000 - val_mae: 523.6874 - lr: 0.0010
Epoch 3/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 1152765.7500 - mae: 555.2532 - val_loss: 826096.5000 - val_mae: 438.9225 - lr: 0.0010
Epoch 4/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 859874.0000 - mae: 468.5569 - val_loss: 583269.9375 - val_mae: 359.6089 - lr: 0.0010
Epoch 5/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 610386.3125 - mae: 394.7771 - val_loss: 417392.0938 - val_mae: 306.6570 - lr: 0.0010
Epoch 6/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 441912.2500 - mae: 341.0423 - val_loss: 322861.5000 - val_mae: 276.8616 - lr: 0.0010

Epoch 51/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 181838.2500 - mae: 227.2201 - val_loss: 173462.5156 - val_mae: 205.6185 - lr: 0.0010
Epoch 52/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180797.5000 - mae: 226.1801 - val_loss: 198346.8438 - val_mae: 218.3862 - lr: 0.0010
Epoch 53/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 181038.0156 - mae: 226.5877 - val_loss: 195691.0469 - val_mae: 216.7337 - lr: 0.0010
Epoch 54/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 181019.7812 - mae: 226.4843 - val_loss: 171521.9375 - val_mae: 203.3398 - lr: 0.0010
Epoch 55/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 181035.0938 - mae: 226.0902 - val_loss: 191286.9531 - val_mae: 214.8756 - lr: 0.0010
Epoch 56/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180878.3906 - mae: 226.0528 - val_loss: 224144.6875 - val_mae: 235.8512 - lr: 0.0010
Epoch 57/1000
10

Epoch 101/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180044.3438 - mae: 224.9620 - val_loss: 184917.3594 - val_mae: 212.0808 - lr: 0.0010
Epoch 102/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180053.2031 - mae: 225.2495 - val_loss: 209938.7969 - val_mae: 224.1900 - lr: 0.0010
Epoch 103/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179961.7812 - mae: 224.7761 - val_loss: 207131.7344 - val_mae: 221.9623 - lr: 0.0010
Epoch 104/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180108.5312 - mae: 225.0951 - val_loss: 198500.1094 - val_mae: 219.2614 - lr: 0.0010
Epoch 105/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179949.7500 - mae: 224.8801 - val_loss: 182281.6719 - val_mae: 210.5564 - lr: 0.0010
Epoch 106/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 180874.0625 - mae: 225.6314 - val_loss: 197259.8594 - val_mae: 219.0284 - lr: 0.0010
Epoch 107/

Epoch 151/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179396.4688 - mae: 224.1501 - val_loss: 185033.7188 - val_mae: 210.4831 - lr: 0.0010
Epoch 152/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179471.7031 - mae: 224.3657 - val_loss: 194193.6562 - val_mae: 215.2432 - lr: 0.0010
Epoch 153/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179632.1562 - mae: 224.2592 - val_loss: 182890.4219 - val_mae: 208.3444 - lr: 0.0010
Epoch 154/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179484.2031 - mae: 223.7955 - val_loss: 170092.6250 - val_mae: 200.9867 - lr: 0.0010
Epoch 155/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179629.4375 - mae: 224.2264 - val_loss: 217467.9375 - val_mae: 229.0391 - lr: 0.0010
Epoch 156/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 179982.1250 - mae: 224.7652 - val_loss: 189202.2656 - val_mae: 213.4433 - lr: 0.0010
Epoch 157/

1089/1089 [==============================] - 1s 1ms/step - loss: 176803.9375 - mae: 220.8943 - val_loss: 186323.1094 - val_mae: 209.4410 - lr: 1.0000e-04
Epoch 249/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 176859.6406 - mae: 220.1528 - val_loss: 190104.2500 - val_mae: 212.2300 - lr: 1.0000e-04
Epoch 250/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 176856.6719 - mae: 220.9574 - val_loss: 192236.2188 - val_mae: 213.2981 - lr: 1.0000e-04
Epoch 251/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 176851.8125 - mae: 220.4157 - val_loss: 192137.6406 - val_mae: 213.2022 - lr: 1.0000e-04
Epoch 252/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 176828.3906 - mae: 220.5546 - val_loss: 188985.7031 - val_mae: 211.0799 - lr: 1.0000e-04
Epoch 253/1000
1089/1089 [==============================] - 1s 1ms/step - loss: 176754.8125 - mae: 220.3074 - val_loss: 183272.5312 - val_mae: 208.2559 - lr: 1.0000e-04
E

In [58]:
# UPAC08 Predictions for Top 2

predict_upacs_top2(model_dictionary=upac08_top2, 
                   upac_name='upac08',
                   X_train=X_train, y_train=y_train,
                   X_val=X_val, y_val=y_val,
                   X_test=X_test, y_test=y_test)

##############

In [60]:
# Optuna for TabNet hyperparameter optimization - Day X, Ghi and CloudOpacity

import optuna
import sklearn

import random

random.seed(69)
np.random.seed(69)
tf.random.set_seed(69)

def optuna_create_model_top3(trial):
    # Do search for n_estimators, max_depth, reg_alpha and reg_lambda
    #sug_layers = trial.suggest_int('num_layers', 1, 4)
    sug_fdim = trial.suggest_int('feature_dim', 32, 72)
    sug_odim = trial.suggest_int('output_dim', 4, 12)
    sug_dsteps = trial.suggest_int('num_decision_steps', 1, 4)
    
    sug_model = StackedTabNetRegressor(feature_columns=None,
                                       num_layers=1, #sug_layers,
                                       num_regressors=1, 
                                       feature_dim=sug_fdim,
                                       num_features=3, 
                                       output_dim=sug_odim,
                                       num_decision_steps=sug_dsteps,
                                       num_groups=1)
    
    return sug_model


def optuna_create_training_top3(model):
    compile_and_fit(model, 
                    X_train['upac08'][['CloudOpacity', 'Ghi', 'Day X']], y_train['upac08'],
                    X_val['upac08'][['CloudOpacity', 'Ghi', 'Day X']], y_val['upac08'],
                    max_epochs=50, rlr_patience=10, es_patience=20)
    
    
def optuna_create_evaluation_top3(model):
    temp_yhat = model.predict(X_val['upac08'][['CloudOpacity', 'Ghi', 'Day X']])
    return sklearn.metrics.mean_squared_error(y_val['upac08'], temp_yhat)
    
    
def objective_top3(trial):
    # Instantiate the model
    temp_model = optuna_create_model_top3(trial)
    
    # Train the model
    optuna_create_training_top3(temp_model)
    
    # Evaluate model
    metrics_val = optuna_create_evaluation_top3(temp_model)
    
    return metrics_val

study_top3 = optuna.create_study(direction='minimize')
study_top3.optimize(objective_top3, n_trials=100, show_progress_bar=True)

[I 2022-08-03 14:45:21,444] A new study created in memory with name: no-name-a9c2cd50-5221-494c-837d-83ad45833f30
c:\users\feel\jupyter\ecgomes\upacs_study\venv\lib\site-packages\optuna\progress_bar.py:47: ExperimentalWarning: Progress bar is experimental (supported from v1.2.0). The interface can change in the future.
  self._init_valid()


  0%|          | 0/100 [00:00<?, ?it/s]

Epoch 1/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1623252.3750 - mae: 697.4752 - val_loss: 1209050.7500 - val_mae: 563.1498 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1211971.5000 - mae: 571.7466 - val_loss: 816295.2500 - val_mae: 436.0601 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 787055.3125 - mae: 445.5736 - val_loss: 500479.7188 - val_mae: 331.3252 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 1s 1ms/step - loss: 505163.9375 - mae: 359.4567 - val_loss: 319165.3125 - val_mae: 268.6573 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 1s 1ms/step - loss: 356927.2188 - mae: 308.8469 - val_loss: 237858.8438 - val_mae: 236.3141 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 1s 1ms/step - loss: 282162.2188 - mae: 278.1069 - val_loss: 224197.5469 - val_mae: 232.9240 - lr: 0.0010
Epoch 7/50
1089/1089 [=========

Epoch 21/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166988.7656 - mae: 216.5752 - val_loss: 179703.4531 - val_mae: 207.1743 - lr: 1.0000e-04
Epoch 22/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166899.2500 - mae: 216.4946 - val_loss: 184927.7500 - val_mae: 211.3319 - lr: 1.0000e-04
Epoch 23/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166722.3594 - mae: 216.5034 - val_loss: 186735.1094 - val_mae: 211.6528 - lr: 1.0000e-04
Epoch 24/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166712.1250 - mae: 216.3198 - val_loss: 183888.0156 - val_mae: 209.5942 - lr: 1.0000e-04
Epoch 25/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166627.4375 - mae: 216.2995 - val_loss: 185160.8125 - val_mae: 211.3321 - lr: 1.0000e-04
Epoch 26/50
1089/1089 [==============================] - 4s 4ms/step - loss: 166396.0781 - mae: 215.8042 - val_loss: 180034.2500 - val_mae: 208.7775 - lr: 1.0000e-04
Epoc

1089/1089 [==============================] - 1s 1ms/step - loss: 152404.7812 - mae: 201.5402 - val_loss: 179474.5938 - val_mae: 200.5499 - lr: 1.0000e-04
Epoch 43/50
1089/1089 [==============================] - 1s 1ms/step - loss: 152364.1406 - mae: 201.2192 - val_loss: 176569.2500 - val_mae: 198.5512 - lr: 1.0000e-04
Epoch 44/50
1089/1089 [==============================] - 1s 1ms/step - loss: 152287.8438 - mae: 201.2297 - val_loss: 176094.3281 - val_mae: 198.0511 - lr: 1.0000e-04
Epoch 45/50
1089/1089 [==============================] - 1s 1ms/step - loss: 152228.7344 - mae: 201.3728 - val_loss: 186679.3750 - val_mae: 204.9766 - lr: 1.0000e-04
Epoch 46/50
1089/1089 [==============================] - 1s 1ms/step - loss: 152284.6719 - mae: 201.2296 - val_loss: 181257.2969 - val_mae: 202.2646 - lr: 1.0000e-04
Epoch 47/50
1089/1089 [==============================] - 1s 1ms/step - loss: 152273.7188 - mae: 201.4351 - val_loss: 180659.9531 - val_mae: 201.2410 - lr: 1.0000e-04
[I 2022-08-03 14

...

1089/1089 [==============================] - 2s 2ms/step - loss: 160752.0625 - mae: 209.0427 - val_loss: 181084.4219 - val_mae: 201.1137 - lr: 0.0010
Epoch 21/50
1089/1089 [==============================] - 2s 2ms/step - loss: 160178.4844 - mae: 208.2474 - val_loss: 166672.9219 - val_mae: 191.3525 - lr: 0.0010
Epoch 22/50
1089/1089 [==============================] - 2s 2ms/step - loss: 160540.7344 - mae: 208.3880 - val_loss: 174078.7812 - val_mae: 197.8687 - lr: 0.0010
Epoch 23/50
1089/1089 [==============================] - 2s 2ms/step - loss: 159307.3438 - mae: 207.8294 - val_loss: 213050.9531 - val_mae: 218.4111 - lr: 0.0010
Epoch 24/50
1089/1089 [==============================] - 2s 2ms/step - loss: 158575.5156 - mae: 206.7490 - val_loss: 192799.2500 - val_mae: 210.9907 - lr: 0.0010
Epoch 25/50
1089/1089 [==============================] - 2s 2ms/step - loss: 160029.3594 - mae: 207.9122 - val_loss: 190819.8594 - val_mae: 203.5995 - lr: 0.0010
Epoch 26/50
1089/1089 [=================

Epoch 34/50
1089/1089 [==============================] - 2s 2ms/step - loss: 152104.7969 - mae: 200.9524 - val_loss: 182204.5000 - val_mae: 200.8875 - lr: 1.0000e-04
Epoch 35/50
1089/1089 [==============================] - 2s 2ms/step - loss: 152093.4375 - mae: 200.7624 - val_loss: 181868.1719 - val_mae: 200.4543 - lr: 1.0000e-04
[I 2022-08-03 16:31:04,612] Trial 92 finished with value: 181868.21083771464 and parameters: {'feature_dim': 69, 'output_dim': 11, 'num_decision_steps': 1}. Best is trial 71 with value: 170844.73521970335.
Epoch 1/50
1089/1089 [==============================] - 2s 1ms/step - loss: 1631290.3750 - mae: 699.9613 - val_loss: 1233571.8750 - val_mae: 579.3192 - lr: 0.0010
Epoch 2/50
1089/1089 [==============================] - 1s 1ms/step - loss: 1256293.5000 - mae: 584.7119 - val_loss: 870107.0625 - val_mae: 455.0631 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 1s 1ms/step - loss: 849246.8125 - mae: 464.0705 - val_loss: 560051.3125 - val_mae

Epoch 19/50
1089/1089 [==============================] - 2s 2ms/step - loss: 159085.6719 - mae: 207.3302 - val_loss: 197191.3750 - val_mae: 209.2482 - lr: 0.0010
Epoch 20/50
1089/1089 [==============================] - 2s 2ms/step - loss: 158751.8125 - mae: 206.9326 - val_loss: 182082.1875 - val_mae: 200.6820 - lr: 0.0010
Epoch 21/50
1089/1089 [==============================] - 2s 2ms/step - loss: 158512.6406 - mae: 206.5792 - val_loss: 163038.9375 - val_mae: 188.6519 - lr: 0.0010
Epoch 22/50
1089/1089 [==============================] - 2s 2ms/step - loss: 159040.5625 - mae: 206.8427 - val_loss: 173099.3281 - val_mae: 201.8287 - lr: 0.0010
Epoch 23/50
1089/1089 [==============================] - 2s 2ms/step - loss: 157538.9844 - mae: 205.7800 - val_loss: 213239.1719 - val_mae: 220.1549 - lr: 0.0010
Epoch 24/50
1089/1089 [==============================] - 2s 2ms/step - loss: 157426.3438 - mae: 205.8640 - val_loss: 191024.8438 - val_mae: 208.9449 - lr: 0.0010
Epoch 25/50
1089/1089 [=====

1089/1089 [==============================] - 2s 1ms/step - loss: 1302459.7500 - mae: 598.2365 - val_loss: 917991.0625 - val_mae: 469.9171 - lr: 0.0010
Epoch 3/50
1089/1089 [==============================] - 2s 1ms/step - loss: 911704.6875 - mae: 482.8499 - val_loss: 610983.5000 - val_mae: 369.8188 - lr: 0.0010
Epoch 4/50
1089/1089 [==============================] - 2s 1ms/step - loss: 608876.8125 - mae: 391.1313 - val_loss: 399856.5938 - val_mae: 297.7889 - lr: 0.0010
Epoch 5/50
1089/1089 [==============================] - 2s 1ms/step - loss: 421880.8125 - mae: 331.5283 - val_loss: 273142.5938 - val_mae: 250.6934 - lr: 0.0010
Epoch 6/50
1089/1089 [==============================] - 2s 1ms/step - loss: 325166.2812 - mae: 298.5572 - val_loss: 274101.2500 - val_mae: 257.8415 - lr: 0.0010
Epoch 7/50
1089/1089 [==============================] - 2s 1ms/step - loss: 269571.8438 - mae: 274.0330 - val_loss: 198094.0156 - val_mae: 217.4536 - lr: 0.0010
Epoch 8/50
1089/1089 [======================

Epoch 31/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154464.7969 - mae: 203.7811 - val_loss: 184868.4375 - val_mae: 205.4458 - lr: 1.0000e-04
Epoch 32/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154377.5000 - mae: 203.7900 - val_loss: 183833.2969 - val_mae: 203.9471 - lr: 1.0000e-04
Epoch 33/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154369.8281 - mae: 203.6575 - val_loss: 179338.7656 - val_mae: 201.3511 - lr: 1.0000e-04
Epoch 34/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154284.3906 - mae: 203.6327 - val_loss: 185013.4531 - val_mae: 204.7272 - lr: 1.0000e-04
Epoch 35/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154178.4219 - mae: 203.5979 - val_loss: 185529.0312 - val_mae: 205.2832 - lr: 1.0000e-04
Epoch 36/50
1089/1089 [==============================] - 2s 1ms/step - loss: 154294.7344 - mae: 203.5263 - val_loss: 187679.5000 - val_mae: 206.4746 - lr: 1.0000e-04
Epoc